In [1]:
import sys
sys.path.append("../lib/")

from nltk.corpus import semcor
from nltk.tree import Tree
import itertools
import random
import pandas as pd
import torch
from bert import *
import csv
from nltk.corpus.reader.wordnet import Lemma
from nltk.corpus import wordnet as wn
from nltk.stem import WordNetLemmatizer

import inflect
import os
from scipy.stats import spearmanr, pearsonr
import re
from utils import *


bert = BERTBase()

lemmatizer = WordNetLemmatizer()


INFO:pytorch_pretrained_bert.modeling:loading archive file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased.tar.gz from cache at /Users/gabriellachronis/.pytorch_pretrained_bert/9c41111e2de84547a463fd39217199738d1e3deb72d4fec4399e6e241983c6f0.ae3cef932725ca7a30cdcb93fc6e09150a55e2a130ec7af63975a16c153ae2ba
INFO:pytorch_pretrained_bert.modeling:extracting archive file /Users/gabriellachronis/.pytorch_pretrained_bert/9c41111e2de84547a463fd39217199738d1e3deb72d4fec4399e6e241983c6f0.ae3cef932725ca7a30cdcb93fc6e09150a55e2a130ec7af63975a16c153ae2ba to temp dir /var/folders/9m/vzvx58rs51v_x5nm620fz4xr0000gn/T/tmpu5sl70vm
INFO:pytorch_pretrained_bert.modeling:Model config {
  "attention_probs_dropout_prob": 0.1,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "max_position_embeddings": 512,
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "type_vocab_size": 2,
  "vocab_size": 3

In [2]:
"""
load semcor stats
"""

#uncomment for whole dataset
sents = semcor.sents()
tagged_sents = semcor.tagged_sents( tag = ' sem ' )
words = semcor.words()

In [3]:
def get_senses_in_tagged_sentence(tagged_sentence):
    """
    given a sense-tagged corpus sentence,returns a list of lemmas and senses in that sentence
    """
    res = []
    for chunk in tagged_sentence:
        
        
        chunk_string = ' '.join(chunk.leaves())

        word = chunk_string.lower()
        lemma = lemmatizer.lemmatize(word)
        poss = chunk.pos()
        
        """
        if we find a wordnet sense (function words dont)
        then scoop it up

        """            
        if isinstance(chunk.label() , Lemma):
            sense = chunk.label()
            for wordform, pos in poss:
                res.append((lemma, sense, wordform.lower(), pos))
    # if we get to the end of the loop. we didn't find the word we were looking for
    return res


In [4]:
"""
Next step is to create an index of all of the tokens of a single lemma. 
So, we build a data structure with all of the word forms found in semcor. With each word form,
we store a list of all of the sentences containing it.
"""

class Vividict(dict):
    def __missing__(self, key):
        value = self[key] = type(self)() # retain local pointer to value
        return value                     # faster to return than dict lookup


#word_index = {}

semcor_indices = list(range(0,len(sents)))
#print(semcor_indices)
random.shuffle(semcor_indices)
#print(semcor_indices)



In [5]:
sense_index = Vividict()

# go through the dataset sentence by sentence
for random_index in semcor_indices:

    sentence_id = random_index
    sent = tagged_sents[sentence_id]

    
    # go through the sentence word by word to get semcor senses in it
    for word in sent:
        senses = get_senses_in_tagged_sentence(sent)
        for lemma, sense, wordform, pos in senses:
            sense = str(sense)
            
            if pos != 'NN':
                continue
            # if this is our first time seeing this word, add it to the index and put the sentence id in the entry
            elif wordform not in sense_index[lemma][sense].keys():
                sense_index[lemma][sense][wordform] = {sentence_id}
            # if we have too many instances of this sense, stop
            elif len(sense_index[lemma][sense][wordform]) >= 30:
                continue
            # otherwise add it
            else:
                sense_index[lemma][sense][wordform].add(sentence_id)

In [6]:
"""
let's take a look at it
"""
import pprint
pprint.pprint(sense_index, width=40)

{'0': {"Lemma('zero.n.02.0')": {'0': {4319,
                                      4334,
                                      4348,
                                      4349,
                                      4352,
                                      4390,
                                      4392,
                                      4456,
                                      4460,
                                      4471,
                                      4475,
                                      4478,
                                      4479,
                                      4550,
                                      4559,
                                      4561,
                                      16180,
                                      16182}}},
 '1': {"Lemma('one.n.01.1')": {'1': {138,
                                     1546,
                                     1565,
                                     4281,
                                

         "Lemma('one.n.01.ace')": {'ace': {4394,
                                           4425,
                                           4432,
                                           4435,
                                           4439},
                                   'aces': {4392,
                                            4424}}},
 'ace of spades': {"Lemma('ace_of_spades.n.01.ace_of_spades')": {'ace': {16550},
                                                                 'of': {16550},
                                                                 'spades': {16550}}},
 'acetone': {"Lemma('acetone.n.01.acetone')": {'acetone': {3998,
                                                           4125,
                                                           4136,
                                                           4142}}},
 'acetonemia': {"Lemma('ketonemia.n.01.acetonemia')": {'acetonemia': {11594,
                                                                

                                                               5540,
                                                               5548,
                                                               5574}}},
 'aerator': {"Lemma('aerator.n.01.aerator')": {'aerator': {5492,
                                                           5518,
                                                           5519,
                                                           5521,
                                                           5537,
                                                           5538,
                                                           5539,
                                                           5553,
                                                           5571,
                                                           5573,
                                                           5575}}},
 'aerial': {"Lemma('forward_pass.n.01.aerial')": {'aerials': {473}}},
 '

               "Lemma('allowance.n.03.allowance')": {'allowance': {12182}},
               "Lemma('allowance.n.04.allowance')": {'allowance': {16174}}},
 'allusion': {"Lemma('allusion.n.01.allusion')": {'allusion': {5344,
                                                               10711},
                                                  'allusions': {4715,
                                                                5407,
                                                                8896,
                                                                14574}}},
 'ally': {"Lemma('ally.n.01.ally')": {'allies': {5648},
                                      'ally': {12975,
                                               14110}},
          "Lemma('ally.n.02.ally')": {'allies': {2539}}},
 'aloe': {"Lemma('aloes.n.01.aloes')": {'aloes': {7522,
                                                  7530}}},
 'aloneness': {"Lemma('aloneness.n.01.aloneness')": {'aloneness': {10528}}},
 'aloof

                                                         'anionics': {3208}}},
 'ankle': {"Lemma('ankle.n.01.ankle')": {'ankle': {330,
                                                   332,
                                                   8693,
                                                   19421},
                                         'ankles': {603,
                                                    7116,
                                                    16601}}},
 'annihilation': {"Lemma('annihilation.n.01.annihilation')": {'annihilation': {12224}}},
 'anniversary': {"Lemma('anniversary.n.01.anniversary')": {'anniversary': {601,
                                                                           9521,
                                                                           11182,
                                                                           11265,
                                                                           12854}}},
 'announcement': 

...

 'ward heelers': {"Lemma('machine_politician.n.01.ward-heeler')": {'heelers': {12658},
                                                                   'ward': {12658}}},
 'ward-heeler': {"Lemma('machine_politician.n.01.ward-heeler')": {'ward-heelers': {1192}}},
 'wardrobe': {"Lemma('wardrobe.n.01.wardrobe')": {'wardrobe': {2698,
                                                               17599}},
              "Lemma('wardrobe.n.02.wardrobe')": {'wardrobe': {694}}},
 'wardroom': {"Lemma('wardroom.n.01.wardroom')": {'wardroom': {19443}}},
 'warehouse': {"Lemma('warehouse.n.01.warehouse')": {'warehouse': {5462,
                                                                   11032,
                                                                   12702},
                                                     'warehouses': {1396,
                                                                    10478}}},
 'warehousing': {"Lemma('repositing.n.01.warehousing')": {'warehousing': {11

 'weave': {"Lemma('weave.n.01.weave')": {'weave': {707},
                                         'weaves': {697}}},
 'web': {"Lemma('vane.n.04.web')": {'web': {10230}},
         "Lemma('web.n.01.web')": {'web': {18951}},
         "Lemma('web.n.02.web')": {'web': {7955}}},
 'wedding': {"Lemma('wedding.n.01.wedding')": {'wedding': {9629,
                                                           19461}}},
 'wedding ceremony': {"Lemma('wedding.n.01.wedding_ceremony')": {'ceremony': {19205},
                                                                 'wedding': {19205}}},
 'wedding day': {"Lemma('wedding_day.n.01.wedding_day')": {'day': {7433,
                                                                   17339},
                                                           'wedding': {7433,
                                                                       17339}}},
 'wedding night': {"Lemma('wedding_night.n.01.wedding_night')": {'night': {19206},
                              

 'window sill': {"Lemma('windowsill.n.01.windowsill')": {'sill': {9148},
                                                         'window': {9148}}},
 'window-washing': {"Lemma('window-washing.n.01.window-washing')": {'window-washing': {8803}}},
 'windowpane': {"Lemma('windowpane.n.01.windowpane')": {'windowpanes': {6366,
                                                                        7848}}},
 'windshield': {"Lemma('windshield.n.01.windshield')": {'windshield': {18703,
                                                                       18853,
                                                                       18951}}},
 'wine': {"Lemma('wine.n.01.wine')": {'wine': {8426,
                                               9186,
                                               9336,
                                               10511,
                                               13107,
                                               13120},
                                    

              "Lemma('workshop.n.02.workshop')": {'workshops': {2033,
                                                                11883}}},
 'worktable': {"Lemma('worktable.n.01.worktable')": {'worktable': {20095}}},
 'world': {"Lemma('earth.n.01.world')": {'world': {1696,
                                                   2294,
                                                   2553,
                                                   2585,
                                                   8767,
                                                   9811,
                                                   10219,
                                                   11203,
                                                   11208,
                                                   11209,
                                                   11210,
                                                   11211,
                                                   11255,
                               

 'yokuts': {"Lemma('mariposan.n.01.Yokuts')": {'yokuts': {16155,
                                                          16157,
                                                          16161,
                                                          16174,
                                                          16175,
                                                          16194,
                                                          16221}}},
 'young': {"Lemma('young.n.01.young')": {'young': {3605,
                                                   3624,
                                                   3711,
                                                   3712,
                                                   3740,
                                                   3762}}},
 'young girls': {"Lemma('lass.n.01.young_girl')": {'girls': {7601},
                                                   'young': {7601}}},
 'young man': {"Lemma('boyfriend.n.01.young_man')": {'man':

In [7]:
"""
Now that we have our word index, we want to construct the evaluation dataset

for each word in the index, we want

We iterate through the words in the dictionary.
we shuffle these indices and access in random order. 
We go through the shuffled indices,
    and we check if we have collected < 50 of this sense.
    if not, we collect this token for the evaluation dataset

collection means:
    we construct a row of data like
        word lemma
        word sense
        token sentence
        
        
at the end we save the data in a csv file called 'semcor_wu_palmer_eval_data.csv'
"""

# def get_sense_in_tagged_sentence(word, tagged_sentence):
#     for chunk in tagged_sentence:

#         chunk_string = ' '.join(chunk.leaves())

#         """
#         if we find the word we're looking for in this chunk,
#         and that chunk has a wordnet sense (function words dont)
#         then scoop it up

#         """            
#         if chunk_string.lower() == word:
#             #print("found %s" % word)
#             #print(chunk.label())

#             #wn_lemma = cunk.label()
#             if isinstance(chunk.label() , Lemma):
#                 return chunk.label()
#     # if we get to the end of the loop. we didn't find the word we were looking for
#     return None


def collect_tokens(indices, sents, tagged_sents):
    """
    takes a word and a list of indices
    returns tuples containing 
        word
        sentence_string
        word_form
        sense
    """
    #sense_count = 0
    tokens = []
    
    # indices is a list of all of the sentence ids containing this word
    indices = list(indices)
    # visit these sentences in random order
    random.shuffle(indices)
    for index in indices[:25]:

        sentence = sents[index]
        sentence = ' '.join(sentence)

        tokens.append(sentence)
        #sense_count += 1
        
        
    
    #print(sense_count.items())
    return tokens


def collect_tokens_for_all_words_to_file(path, sense_index, sents, tagged_sents):
    with open(path, 'w', newline='') as csvfile:
        writer = csv.writer(csvfile)


        for lemma in sense_index.keys():
            #print(lemma)
            for sense in sense_index[lemma].keys():
                print(sense)
                for word_form, indices in sense_index[lemma][sense].items():
                    #print(lemma)
                    #print(sense)
                    #print(indices)


                    frequency = len(indices)
                    tokens = collect_tokens(indices, sents, tagged_sents)
                    #print(tokens)
                    #raise Exception("nfwip")

                    for token in tokens:
                        row = (lemma, sense, word_form, token)
                        writer.writerow(row)                    
                    #sensewriter.writerow(sense_count.items())



collect_tokens_for_all_words_to_file('../data/semcor_eval_data_11_27_2021.csv', sense_index, sents, tagged_sents)



Lemma('communication.n.01.communication')
Lemma('communication.n.03.communication')
Lemma('communication.n.02.communication')
Lemma('kind.n.01.form')
Lemma('form.n.01.form')
Lemma('form.n.03.form')
Lemma('shape.n.01.form')
Lemma('shape.n.02.form')
Lemma('human_body.n.01.form')
Lemma('form.n.11.form')
Lemma('form.n.08.form')
Lemma('form.n.09.form')
Lemma('form.n.10.form')
Lemma('form.n.07.form')
Lemma('language.n.01.language')
Lemma('lyric.n.01.language')
Lemma('speech.n.02.language')
Lemma('linguistic_process.n.02.language')
Lemma('language.n.05.language')
Lemma('structure.n.01.structure')
Lemma('structure.n.03.structure')
Lemma('structure.n.02.structure')
Lemma('structure.n.04.structure')
Lemma('answer.n.01.reply')
Lemma('mate.n.01.mate')
Lemma('teammate.n.01.mate')
Lemma('mate.n.03.mate')
Lemma('spouse.n.01.mate')
Lemma('match.n.04.mate')
Lemma('disloyalty.n.01.disloyalty')
Lemma('feature.n.01.feature')
Lemma('feature.n.02.feature')
Lemma('feature.n.03.feature')
Lemma('land.n.01.land

Lemma('day.n.04.day')
Lemma('day.n.05.day')
Lemma('day.n.06.day')
Lemma('measure.n.01.step')
Lemma('footstep.n.03.step')
Lemma('stairs.n.01.steps')
Lemma('step.n.03.step')
Lemma('step.n.04.step')
Lemma('steps.n.02.steps')
Lemma('gradation.n.01.step')
Lemma('dictionary.n.01.dictionary')
Lemma('use.n.01.usage')
Lemma('custom.n.01.usage')
Lemma('information.n.01.information')
Lemma('information.n.02.information')
Lemma('text.n.01.text')
Lemma('list.n.01.list')
Lemma('tilt.n.04.list')
Lemma('cell.n.01.cell')
Lemma('cell.n.02.cell')
Lemma('cell.n.03.cell')
Lemma('ordering.n.01.order')
Lemma('orderliness.n.02.order')
Lemma('club.n.02.order')
Lemma('order.n.07.order')
Lemma('order.n.09.order')
Lemma('order.n.02.order')
Lemma('order.n.03.order')
Lemma('order.n.01.order')
Lemma('decree.n.01.order')
Lemma('happening.n.01.occurrence')
Lemma('occurrence.n.02.occurrence')
Lemma('light.n.02.light')
Lemma('light.n.01.light')
Lemma('light.n.05.light')
Lemma('light.n.10.light')
Lemma('light.n.07.light'

Lemma('coating.n.01.coat')
Lemma('easter.n.01.Easter')
Lemma('bonnet.n.01.bonnet')
Lemma('bicycle.n.01.bicycle')
Lemma('junior.n.01.junior')
Lemma('junior_high_school.n.01.junior_high_school')
Lemma('junior.n.02.junior')
Lemma('junior_high_school.n.01.junior_high')
Lemma('junior.n.03.junior')
Lemma('department_store.n.01.department_store')
Lemma('selection.n.02.selection')
Lemma('choice.n.02.selection')
Lemma('choice.n.01.selection')
Lemma('denture.n.01.denture')
Lemma('example.n.01.example')
Lemma('model.n.07.example')
Lemma('exemplar.n.01.example')
Lemma('example.n.04.example')
Lemma('conqueror.n.01.conqueror')
Lemma('denmark.n.01.Denmark')
Lemma('child.n.01.child')
Lemma('child.n.02.child')
Lemma('voltaire.n.01.Voltaire')
Lemma('predicament.n.01.predicament')
Lemma('rousseau.n.01.Rousseau')
Lemma('fad.n.01.furor')
Lemma('discourse.n.01.discourse')
Lemma('title.n.07.title')
Lemma('title.n.01.title')
Lemma('title.n.06.title')
Lemma('title.n.02.title')
Lemma('title.n.03.title')
Lemma('

Lemma('opinion.n.01.sentiment')
Lemma('patriotism.n.01.nationalism')
Lemma('nationalism.n.02.nationalism')
Lemma('firm.n.01.firm')
Lemma('enzyme.n.01.enzyme')
Lemma('formulation.n.01.preparation')
Lemma('preparation.n.01.preparation')
Lemma('planning.n.03.preparation')
Lemma('feed.n.01.feed')
Lemma('manufacturer.n.01.manufacturer')
Lemma('manufacturer.n.02.manufacturer')
Lemma('load.n.01.load')
Lemma('load.n.05.load')
Lemma('load.n.04.load')
Lemma('cargo.n.01.load')
Lemma('load.n.02.load')
Lemma('realization.n.01.realization')
Lemma('realization.n.02.realization')
Lemma('military_officer.n.01.officer')
Lemma('officeholder.n.01.officer')
Lemma('policeman.n.01.officer')
Lemma('officer.n.04.officer')
Lemma('noncommissioned_officer.n.01.noncom')
Lemma('cavalryman.n.01.trooper')
Lemma('trooper.n.02.trooper')
Lemma('good.n.01.good')
Lemma('good.n.02.good')
Lemma('good.n.03.good')
Lemma('regiment.n.01.regiment')
Lemma('dollar.n.01.dollar')
Lemma('dollar.n.02.dollar')
Lemma('art.n.01.art')
Lem

Lemma('end.n.09.end')
Lemma('end.n.08.end')
Lemma('end.n.06.end')
Lemma('end.n.10.end')
Lemma('finger.n.01.finger')
Lemma('vote.n.02.vote')
Lemma('vote.n.01.vote')
Lemma('right_to_vote.n.01.vote')
Lemma('saturday.n.01.Saturday')
Lemma('election.n.01.election')
Lemma('election.n.02.election')
Lemma('increase.n.03.increase')
Lemma('increase.n.04.increase')
Lemma('addition.n.03.increase')
Lemma('increase.n.02.increase')
Lemma('increase.n.05.increase')
Lemma('prestige.n.01.prestige')
Lemma('conversion.n.04.conversion')
Lemma('conversion.n.01.conversion')
Lemma('conversion.n.03.conversion')
Lemma('conversion.n.02.conversion')
Lemma('tractarian.n.01.Tractarian')
Lemma('section.n.04.segment')
Lemma('england.n.01.England')
Lemma('percentage.n.01.percent')
Lemma('hearing.n.02.hearing')
Lemma('hearing.n.01.hearing')
Lemma('earshot.n.01.hearing')
Lemma('listening.n.01.hearing')
Lemma('populace.n.01.public')
Lemma('public.n.02.public')
Lemma('male.n.01.male')
Lemma('male.n.02.male')
Lemma('aeratio

...

Lemma('block_letter.n.01.block_capital')
Lemma('materiality.n.02.corporeality')
Lemma('graining.n.01.woodgraining')
Lemma('wording.n.01.wording')
Lemma('lastingness.n.01.durability')
Lemma('pulse.n.03.heart_rate')
Lemma('villain.n.01.villain')
Lemma('villain.n.02.villain')
Lemma('van_der_waal's_forces.n.01.van_der_Waal's_forces')
Lemma('specific_heat.n.01.specific_heat')
Lemma('frog.n.01.frog')
Lemma('resistance_thermometer.n.01.resistance_thermometer')
Lemma('dove.n.01.dove')
Lemma('magpie.n.01.magpie')
Lemma('jackdaw.n.01.jackdaw')
Lemma('harpy.n.04.harpy_eagle')
Lemma('conditional_reflex.n.01.conditioned_response')
Lemma('contemplation.n.02.musing')
Lemma('fedora.n.01.Stetson')
Lemma('moderation.n.01.moderation')
Lemma('irritation.n.01.irritation')
Lemma('sneer.n.01.sneer')
Lemma('laxness.n.01.laxness')
Lemma('day.n.04.daytime')
Lemma('droppings.n.01.dung')
Lemma('lion.n.01.lion')
Lemma('northwest.n.01.Northwest')
Lemma('china.n.01.Communist_China')
Lemma('field_goal.n.01.field_goal

Lemma('master_of_ceremonies.n.01.master_of_ceremonies')
Lemma('suitability.n.01.suitability')
Lemma('trope.n.01.figure_of_speech')
Lemma('calcification.n.01.calcification')
Lemma('freedom_of_thought.n.01.freedom_of_thought')
Lemma('political_system.n.01.form_of_government')
Lemma('supporter.n.01.admirer')
Lemma('land.n.04.terra_firma')
Lemma('pillar.n.01.pillar')
Lemma('icelandic.n.01.Icelandic')
Lemma('thirties.n.01.mid-thirties')
Lemma('public_opinion.n.01.public_opinion')
Lemma('stiffening.n.01.stiffening')
Lemma('streetcar.n.01.streetcar')
Lemma('circular.n.01.broadside')
Lemma('gun_smoke.n.01.gun_smoke')
Lemma('worsted.n.01.worsted')
Lemma('herringbone.n.01.herringbone')
Lemma('lapel.n.01.lapel')
Lemma('confessor.n.01.confessor')
Lemma('consumption.n.01.consumption')
Lemma('magazine_article.n.01.magazine_article')
Lemma('dead_person.n.01.deceased')
Lemma('postmaster_general.n.01.postmaster_general')
Lemma('witch_doctor.n.01.witch_doctor')
Lemma('kick_up.n.01.kick_up')
Lemma('linco

Lemma('car_door.n.01.car_door')
Lemma('social_welfare.n.01.social_welfare')
Lemma('cash_register.n.01.cash_register')
Lemma('liner.n.01.line_drive')
Lemma('shovel.n.01.shovel')
Lemma('three-hitter.n.01.3-hitter')
Lemma('land_grant.n.01.land_grant')
Lemma('aperture.n.01.aperture')
Lemma('bevy.n.01.bevy')
Lemma('laager.n.01.lager')
Lemma('work_camp.n.01.work_camp')
Lemma('concentration_camp.n.01.concentration_camp')
Lemma('politician.n.02.political_leader')
Lemma('kilohertz.n.01.kc')
Lemma('milliequivalent.n.01.meq')
Lemma('quadriceps.n.01.quadriceps')
Lemma('reclining.n.01.reclining')
Lemma('marker.n.01.marker')
Lemma('monograph.n.01.monograph')
Lemma('temperature_gradient.n.01.temperature_gradient')
Lemma('dewar_flask.n.01.Dewar')
Lemma('advertising_agency.n.01.advertising_agency')
Lemma('installment_plan.n.01.time_plan')
Lemma('lurch.n.01.lurch')
Lemma('adeptness.n.01.quickness')
Lemma('sweater.n.01.sweater')
Lemma('military.n.01.military')
Lemma('aircraft_carrier.n.01.aircraft_carrie

Lemma('tiger.n.01.tiger')
Lemma('tiger.n.02.tiger')
Lemma('verdict.n.01.verdict')
Lemma('year-end.n.01.year-end')
Lemma('holy_eucharist.n.01.Holy_Sacrament')
Lemma('epic_poem.n.01.epic_poem')
Lemma('pantheon.n.01.pantheon')
Lemma('political_unit.n.01.political_unit')
Lemma('self-awareness.n.01.self-awareness')
Lemma('insurance_claim.n.01.insurance_claim')
Lemma('manor.n.01.manor_house')
Lemma('pageant.n.01.pageant')
Lemma('mosaic.n.01.mosaic')
Lemma('applicability.n.01.pertinence')
Lemma('junction.n.01.junction')
Lemma('whole-word_method.n.01.whole-word_method')
Lemma('pen-and-ink.n.01.pen-and-ink')
Lemma('jeweler's_glass.n.01.jeweler's_glass')
Lemma('midwest.n.01.middle_west')
Lemma('octahedron.n.01.octahedron')
Lemma('catch.n.01.catch')
Lemma('hometown.n.01.hometown')
Lemma('reception_room.n.01.reception_room')
Lemma('craze.n.02.delirium')
Lemma('malice.n.01.spite')
Lemma('defamation.n.01.calumny')
Lemma('whig.n.01.Whig')
Lemma('cleat.n.01.cleat')
Lemma('sock.n.01.sock')
Lemma('indef

Lemma('warren.n.04.rabbit_warren')
Lemma('paramagnet.n.01.paramagnet')
Lemma('new_year's_eve.n.01.December_31')
Lemma('epigram.n.01.epigram')
Lemma('freeze.n.01.freezing')
Lemma('thaw.n.01.thawing')
Lemma('sum.n.05.aggregate')
Lemma('hebrew.n.01.Hebrew')
Lemma('electric_shock.n.03.electrical_shock')
Lemma('cold_sweat.n.01.cold_sweat')
Lemma('punster.n.01.punster')
Lemma('tease.n.01.tease')
Lemma('disinterest.n.01.disinterest')
Lemma('makeready.n.01.makeready')
Lemma('pharmacist.n.01.pharmacist')
Lemma('aviation.n.01.aviation')
Lemma('gasoline.n.01.gasoline')
Lemma('franc.n.01.franc')
Lemma('lineman.n.01.lineman')
Lemma('feedback.n.02.feedback')
Lemma('digitalization.n.01.digitalization')
Lemma('anticoagulation.n.01.anticoagulation')
Lemma('original_sin.n.01.original_sin')
Lemma('hard_times.n.01.hard_times')
Lemma('textbook.n.01.school_text')
Lemma('thwart.n.01.thwart')
Lemma('astrophysics.n.01.astrophysics')
Lemma('medical_school.n.01.medical_school')
Lemma('stagnation.n.01.stagnation'